In [2]:
# Dynamically add project root to sys.path
import sys
import os
sys.path.append(os.getcwd())
from data_pipelines.daily_pipeline import run_daily_pipeline
from data_pipelines.save_to_db import save_all_to_db
import pandas as pd
%load_ext autoreload
%autoreload 2


In [3]:
movies_df = pd.read_pickle('data_pipelines/temp_data/movies.pkl')

In [7]:
screenings_df, cinemas_df = run_daily_pipeline()

save_all_to_db(cinemas_df, movies_df, screenings_df)

INFO:root:Starting daily data pipeline...
INFO:WDM:====== WebDriver manager ======
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Driver [/Users/ardsnijders/.wdm/drivers/chromedriver/mac64/133.0.6943.141/chromedriver-mac-x64/chromedriver] found in cache


/Users/ardsnijders/Documents/cineville_scraper/backend


In [2]:
from data_pipelines.save_to_db import get_existing_movies

movies = get_existing_movies()

In [3]:
movies

{('10 things i hate about you', 1999),
 ('a complete unknown', 2024),
 ('a real pain', 2024),
 ('about dry grasses', 2023),
 ('all we imagine as light', 2024),
 ('alpha', 2024),
 ('als de kraanvogels overvliegen', 1957),
 ('amal', 2023),
 ('anora', 2024),
 ('attack on titan: the last attack', 2024),
 ('babygirl', 2024),
 ('becoming led zeppelin', 2025),
 ('before sunrise', 1995),
 ('before sunset', 2004),
 ('belle de jour', 1967),
 ('blue velvet', 1986),
 ('bottoms', 2023),
 ('bridget jones: mad about the boy', 2025),
 ('call me agnes', 2024),
 ('captain america: brave new world 2d', 2025),
 ('caught by the tides', 2024),
 ('climates', 2006),
 ('companion', 2025),
 ('conclave', 2024),
 ('confidenza', 2023),
 ('dahomey', 2024),
 ('david lynch: the art life', 2016),
 ('de eeuw van simeon ten holt', 2025),
 ('dead poets society', 1989),
 ('den of thieves: pantera', 2025),
 ('diamant brut', 2024),
 ('dikkie dik 2: een nieuwe vriend voor dikkie dik', 2024),
 ('dragon ball z: battle of gods'

### Pipeline, step by step

In [17]:
import logging
import pandas as pd
from data_pipelines.scrapers.filmladder import FilmladderScraper
from data_pipelines.daily_pipeline import assign_ids_cinemas, assign_ids_screenings, extract_unique_movies
from data_pipelines.daily_pipeline import add_cineville_tag, add_imdb_links, clean_screenings, get_new_movies
from data_pipelines.save_to_db import save_movies, save_screenings, save_cinemas
# from external.imdb_api import fetch_imdb_metadata
from data_pipelines.save_to_db import get_existing_movies

%load_ext autoreload
%autoreload 2

logging.basicConfig(level=logging.INFO)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [112]:
logging.info("Starting daily data pipeline...")

# 1️⃣ Scrape Filmladder (returns two DataFrames)
filmladder = FilmladderScraper()
screenings_df, cinemas_df = filmladder.run()

INFO:root:Starting daily data pipeline...
INFO:WDM:====== WebDriver manager ======
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Driver [/Users/ardsnijders/.wdm/drivers/chromedriver/mac64/133.0.6943.141/chromedriver-mac-x64/chromedriver] found in cache


<html lang="nl"><head>
    <!-- Google tag (gtag.js) -->
    <script async="" src="//c.amazon-adsystem.com/aax2/apstag.js"></script><script async="" src="//resources.planetnine.com/player/latest/Pnvp.js?t=0.3149822278312746&amp;h=www.filmladder.nl"></script><script async="" src="https://www.googletagmanager.com/gtag/js?id=G-FXGH1XSDLV"></script>
    <script>
      window.dataLayer = window.dataLayer || [];
      function gtag(){dataLayer.push(arguments);}
      gtag('js', new Date());

      gtag('config', 'G-FXGH1XSDLV');
    </script>

    <meta charset="utf-8">
    <meta http-equiv="X-UA-Compatible" content="IE=edge">
    <meta name="viewport" content="width=device-width">
    <meta name="theme-color" content="#FFCC02">

    <link rel="apple-touch-icon-precomposed" type="image/png" href="/assets/apple-touch-icon-144x144-af857028c3108d31c1be3c58e48fb488b2aee4fe36160f5a674fa708427176df.png" sizes="144x144">
    <link rel="apple-touch-icon-precomposed" type="image/png" href="/assets/ap

In [114]:
# 2️⃣ Assign IDs
screenings_df = assign_ids_screenings(screenings_df)
screenings_df = clean_screenings(screenings_df)
cinemas_df = add_cineville_tag(assign_ids_cinemas(cinemas_df))

/Users/ardsnijders/Documents/cineville_scraper/backend


In [115]:
scraped_movies = extract_unique_movies(screenings_df)

In [116]:
scraped_movies

movie_id                           title  year  \
0    378909531a                       favoriten  2024   
1    430904b120                          merckx  2025   
2    e7bc07ba2a              a complete unknown  2024   
3    ff1d83f7ce                           alpha  2024   
4    172e369640                           anora  2024   
..          ...                             ...   ...   
156  74c1d8b113  marcel the shell with shoes on  2021   
157  3927581269               memoir of a snail  2024   
158  767834fde2                  paths of glory  1957   
159  42e553e73d                         platoon  1986   
160  20a1327ff2      the seed of the sacred fig  2024   

                                            movie_link  
0    https://www.filmladder.nl/film/favoriten-2024/...  
1    https://www.filmladder.nl/film/merckx-2025/pop...  
2    https://www.filmladder.nl/film/a-complete-unkn...  
3    https://www.filmladder.nl/film/alpha-2024/popu...  
4    https://www.filmladder.nl/film/anora-2024/popu...  
..                                                 ...  
156  https://www.filmladder.nl/film/marcel-the-shel...  
157  https://www.filmladder.nl/film/memoir-of-a-sna...  
158  https://www.filmladder.nl/film/paths-of-glory-...  
159  https://www.filmladder.nl/film/platoon-1986/po...  
160  https://www.filmladder.nl/film/the-seed-of-the...  

[161 rows x 4 columns]

In [129]:
from data_pipelines.daily_pipeline import get_new_movies
new_movies = get_new_movies(scraped_movies=scraped_movies)
new_movies = new_movies.sample(7)
new_movies


movie_id                                  title  year  \
144  ecef72462c              sonic the hedgehog 3 (ov)  2024   
125  dde3515e06             paddington in peru (nl) 2d  2024   
136  fd8c69f8be    captain america: brave new world 3d  2025   
149  2e37f5ff60          mufasa: the lion king (ov) 3d  2024   
126  0372dd54db             paddington in peru (ov) 2d  2024   
137  2dba63aeb9  captain america: brave new world imax  2025   
124  6abeca5aea          mufasa: the lion king (ov) 2d  2024   

                                            movie_link  
144  https://www.filmladder.nl/film/sonic-the-hedge...  
125  https://www.filmladder.nl/film/paddington-in-p...  
136  https://www.filmladder.nl/film/captain-america...  
149  https://www.filmladder.nl/film/mufasa-the-lion...  
126  https://www.filmladder.nl/film/paddington-in-p...  
137  https://www.filmladder.nl/film/captain-america...  
124  https://www.filmladder.nl/film/mufasa-the-lion...

In [ ]:
from data_pipelines.scrapers.imdb import IMDBFetcher
scraper = IMDBFetcher(headless=True)
new_movies = scraper.run(new_movies)

INFO:WDM:====== WebDriver manager ======
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Driver [/Users/ardsnijders/.wdm/drivers/chromedriver/mac64/133.0.6943.141/chromedriver-mac-x64/chromedriver] found in cache
Scraping Progress: 100%|██████████| 7/7 [00:13<00:00,  1.98s/it]


In [133]:
new_movies

movie_id                                title  year  \
0  ecef72462c            sonic the hedgehog 3 (ov)  2024   
1  dde3515e06           paddington in peru (nl) 2d  2024   
2  fd8c69f8be  captain america: brave new world 3d  2025   
4  2e37f5ff60        mufasa: the lion king (ov) 3d  2024   

                                          movie_link  \
0  https://www.filmladder.nl/film/sonic-the-hedge...   
1  https://www.filmladder.nl/film/paddington-in-p...   
2  https://www.filmladder.nl/film/captain-america...   
4  https://www.filmladder.nl/film/mufasa-the-lion...   

                               imdb_link  
0  https://www.imdb.com/title/tt18259086  
1   https://www.imdb.com/title/tt5822536  
2  https://www.imdb.com/title/tt14513804  
4  https://www.imdb.com/title/tt13186482

In [135]:
from data_pipelines.scrapers.imdb import IMDBScraper
scraper = IMDBScraper(headless=True)
enriched_new_movies = scraper.run(new_movies)

INFO:WDM:====== WebDriver manager ======
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Get LATEST chromedriver version for google-chrome
INFO:WDM:Driver [/Users/ardsnijders/.wdm/drivers/chromedriver/mac64/133.0.6943.141/chromedriver-mac-x64/chromedriver] found in cache
Scraping IMDb Metadata:   0%|          | 0/4 [00:00<?, ?it/s]

<html lang="en-US" xmlns:og="http://opengraphprotocol.org/schema/" xmlns:fb="http://www.facebook.com/2008/fbml"><head><script async="" src="https://sb.scorecardresearch.com/beacon.js"></script><script async="" src="https://images-na.ssl-images-amazon.com/images/I/31wEJw-CHxL.js" crossorigin="anonymous"></script><meta charset="utf-8"><meta name="viewport" content="width=device-width"><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><title>Sonic the Hedgehog 3 (2024) - IMDb</title><meta name="description" content="Sonic the Hedgehog 3: Directed by Jeff Fowler. With Jim Carrey, Ben Schwartz, Keanu Reeves, Idris Elba. Sonic, Knuckles, and Tails reunite against a powerful new adversary, Shadow, a mysterious villain with powers unlike anything they have faced before. With their abilities outmatched, Team Sonic must seek out an unlikely alliance." data-id="main"><meta name="keywords" content="Reviews, Showtimes, DVDs, Photos, User Ratings, Synopsis, Trailers, 

Scraping IMDb Metadata:  25%|██▌       | 1/4 [00:04<00:14,  4.84s/it]

<html lang="en-US" xmlns:og="http://opengraphprotocol.org/schema/" xmlns:fb="http://www.facebook.com/2008/fbml"><head><script async="" src="https://sb.scorecardresearch.com/beacon.js"></script><script async="" src="https://images-na.ssl-images-amazon.com/images/I/31wEJw-CHxL.js" crossorigin="anonymous"></script><meta charset="utf-8"><meta name="viewport" content="width=device-width"><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><title>Paddington in Peru (2024) - IMDb</title><meta name="description" content="Paddington in Peru: Directed by Dougal Wilson. With Ben Whishaw, Imelda Staunton, Oliver Maltman, Joel Fry. Paddington returns to Peru to visit his beloved Aunt Lucy, who now resides at the Home for Retired Bears. With the Brown family in tow, a thrilling adventure ensues when a mystery plunges them into an unexpected journey." data-id="main"><meta name="keywords" content="Reviews, Showtimes, DVDs, Photos, User Ratings, Synopsis, Trailers, Credits

Scraping IMDb Metadata:  50%|█████     | 2/4 [00:09<00:09,  4.82s/it]

<html lang="en-US" xmlns:og="http://opengraphprotocol.org/schema/" xmlns:fb="http://www.facebook.com/2008/fbml"><head><script async="" src="https://sb.scorecardresearch.com/beacon.js"></script><script async="" src="https://images-na.ssl-images-amazon.com/images/I/31wEJw-CHxL.js" crossorigin="anonymous"></script><meta charset="utf-8"><meta name="viewport" content="width=device-width"><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><title>Captain America: Brave New World (2025) - IMDb</title><meta name="description" content="Captain America: Brave New World: Directed by Julius Onah. With Anthony Mackie, Harrison Ford, Danny Ramirez, Shira Haas. Sam Wilson, the new Captain America, finds himself in the middle of an international incident and must discover the motive behind a nefarious global plan." data-id="main"><meta name="keywords" content="Reviews, Showtimes, DVDs, Photos, User Ratings, Synopsis, Trailers, Credits"><meta name="robots" content="max-ima

Scraping IMDb Metadata:  75%|███████▌  | 3/4 [00:16<00:05,  5.60s/it]

<html lang="en-US" xmlns:og="http://opengraphprotocol.org/schema/" xmlns:fb="http://www.facebook.com/2008/fbml"><head><script async="" src="https://sb.scorecardresearch.com/beacon.js"></script><script async="" src="https://images-na.ssl-images-amazon.com/images/I/31wEJw-CHxL.js" crossorigin="anonymous"></script><meta charset="utf-8"><meta name="viewport" content="width=device-width"><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><title>Mufasa: The Lion King (2024) - IMDb</title><meta name="description" content="Mufasa: The Lion King: Directed by Barry Jenkins. With Aaron Pierre, Kelvin Harrison Jr., Tiffany Boone, Kagiso Lediga. Mufasa, a cub lost and alone, meets a sympathetic lion named Taka, the heir to a royal bloodline. The chance meeting sets in motion an expansive journey of a group of misfits searching for their destiny." data-id="main"><meta name="keywords" content="Reviews, Showtimes, DVDs, Photos, User Ratings, Synopsis, Trailers, Credits">

Scraping IMDb Metadata: 100%|██████████| 4/4 [00:21<00:00,  5.40s/it]


In [136]:
enriched_new_movies

movie_id                              title_x year_x  \
0  ecef72462c            sonic the hedgehog 3 (ov)   2024   
1  dde3515e06           paddington in peru (nl) 2d   2024   
2  fd8c69f8be  captain america: brave new world 3d   2025   
3  2e37f5ff60        mufasa: the lion king (ov) 3d   2024   

                                          movie_link  \
0  https://www.filmladder.nl/film/sonic-the-hedge...   
1  https://www.filmladder.nl/film/paddington-in-p...   
2  https://www.filmladder.nl/film/captain-america...   
3  https://www.filmladder.nl/film/mufasa-the-lion...   

                               imdb_link title_y year_y rating genres  
0  https://www.imdb.com/title/tt18259086     NaN    NaN    NaN    NaN  
1   https://www.imdb.com/title/tt5822536     NaN    NaN    NaN    NaN  
2  https://www.imdb.com/title/tt14513804     NaN    NaN    NaN    NaN  
3  https://www.imdb.com/title/tt13186482     NaN    NaN    NaN    NaN

In [109]:
new_movies = new_movies[~new_movies["imdb_link"].isin(set(existing_movies["imdb_link"].dropna()))]



In [111]:
save_movies(new_movies)

In [ ]:
# 3️⃣ Extract and fetch IMDb metadata for unique movies
# TODO: first reference movies_df with existing movies sqlite backend.
# only fetch IMDB links for new titles.
# movies_df = extract_unique_movies(screenings_df)

# movies_df = fetch_metadata(movies_df)

# # 4️⃣ Store data in the database
# save_movies(movies_df)
# save_screenings(screenings_df)
# save_cinemas(cinemas_df)

logging.info("Daily data pipeline completed.")